In [ ]:
# System_seed table info
dbutils.widgets.text("System_Id", "")
dbutils.widgets.text("tb_system_seed", "")

# Container Mounting credentials and info
dbutils.widgets.text("storage_account_name", "")
dbutils.widgets.text("storage_account_access_key", "")

# Cosmos DB credentials and info
dbutils.widgets.text("cosmosDBaccount", "")
dbutils.widgets.text("cosmosMasterKey", "")


In [1]:
# System_seed table info
System_Id = int(dbutils.widgets.get("System_Id"))
tb_system_seed = dbutils.widgets.get("tb_system_seed")

# Container Mounting credentials and info
storage_account_name = dbutils.widgets.get("storage_account_name")
storage_account_access_key = dbutils.widgets.get("storage_account_access_key")

# Cosmos DB credentials and info
cosmosDBaccount = dbutils.widgets.get("cosmosDBaccount")
cosmosMasterKey = dbutils.widgets.get("cosmosMasterKey")

print(System_Id)
print(storage_account_name)
print(storage_account_access_key)
print(cosmosDBaccount)
print(tb_system_seed)

NameError: name 'dbutils' is not defined

In [ ]:
# dbutils.widgets.remove("cosmosContainerName")

In [ ]:
system_id = System_Id
records_read=0
record_inserted=0
df=""
trigged_by = dbutils.notebook.entry_point.getDbutils().notebook().getContext().userName().get()

In [ ]:
from pyspark.sql import SparkSession
from pyspark.sql.utils import AnalysisException

spark = SparkSession.builder.getOrCreate()

# This code is used to retrieve file and database information from the tb_system_seed table using a Spark SQL query, and handle exceptions while capturing execution result information for notebook termination.

try:
    # Execute the Spark SQL query
    file_info = spark.sql("""
        SELECT *
        FROM {}
        WHERE System_Id = {}
    """.format(tb_system_seed, System_Id)).first()

    if file_info is None:
        raise ValueError("File details not found in system_seed table for system_id = {}".format(System_Id))

    source_db_container_name = file_info.Source_DB
    source_object_name = file_info.Source_Object_Name
    cosmosDatabaseName = file_info.Target_DB
    cosmosContainerName = file_info.Target_Object_Name
    source_Type = file_info.Source_Type	
    target_Type = file_info.Target_Type
    isDelta = file_info.IsDelta	
    delta_Field = file_info.Delta_Field

    print(source_db_container_name)
    print(source_object_name)
    print(cosmosDatabaseName)
    print(cosmosContainerName)
    print(source_Type)
    print(target_Type)
    print(isDelta)
    print(delta_Field)
except (AnalysisException, ValueError, Exception) as error:
    # print("Error occurred while processing system_seed input:")
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception": str(error),"system_id":system_id}
    dbutils.notebook.exit(my_json)

curated
account_table_details
BankingDataset
account_details
delta
cosmos.oltp
True
id


In [ ]:
try:
     # Mount an Azure Blob Storage container as a file system in Databricks
    dbutils.fs.mount(
        source=f"wasbs://{source_db_container_name}@{storage_account_name}.blob.core.windows.net",
        mount_point=f"/mnt/{source_db_container_name}",
        extra_configs={
            f"fs.azure.account.key.{storage_account_name}.blob.core.windows.net": storage_account_access_key
        },
    )
    print("Mount successful!")
except Exception as e:
     # If the mount is already present, catch the exception and print the error message
    print(f"Already Mounted {str(e).partition('is:')[0]}")

Already Mounted An error occurred while calling o1555.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/curated; nested exception 


In [ ]:
# This code is used to read a file from a specified Blob Storage container, load it into a DataFrame, display the count and contents of the DataFrame, while handling any exceptions and capturing execution result information for notebook termination.

def read_file(source_db_container_name, source_object_name):
    if source_Type == "csv":
        # If the file type is CSV, construct the path with the specified container, object name, and file type
        path = f"dbfs:/mnt/{source_db_container_name}/{source_object_name}.{source_Type}"
    else:
        # For other delta file types, construct the path without the file type extension
        path = f"dbfs:/mnt/{source_db_container_name}/{source_object_name}"
   
    df = spark.read.format(source_Type).option("header", "true").load(path)
    display(df.count())
    display(df)
    return df
try:
    df = read_file(source_db_container_name, source_object_name)
    records_read=df.count()
except Exception as exp:
    exp=str(exp)
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
     # Terminate the notebook execution and provide the JSON object as the exit value
    dbutils.notebook.exit(my_json)

10000

id Member ID Merchant ID Transaction ID Amount of Transaction in US Dollars Expr_acct_crd Transaction Authentication date Transaction Date Original Amount of Transaction Amount Transaction Central Processing Date Conversion Date PS2000 Authentication Amount Interchange Percentage rate Interchange Percentage Intermediate rate Authentication Cdt Authentication_Ctm Transaction Detail Indicator Additional Data Indicator Debit ACH indicator Fraud Segment Number Merchant Volume Indicator Transaction Description Merchant Flag PS2000 Transaction ID Source Decimal Conversion Rate Transaction Markup Amount TLP_Type Transaction Register Number Receipt Number TLP_Transaction Expiry Date National Reimbursement Fee Merchant DBA Name Merchant DBA City Merchant DBA State Merchant DBA Country Merchant Number Pcas_Flag cwb_Code Floor limit code Mail Phone Code Authorisation Code Trmnl_Capability Card Holder ID Code Reimbursement Attribute Code ATM Account Select Authorisation Character Indicator Payment Service ID Class Code Debit Credit Indicator Merchant Terminal Indicator Interchange Qualify Banknet Reference Number PS2000 Authorization Currency PS2000 Authorization Respondent Code ISO Address Verification Result Credit Account_Ved Term ID Non Print Flag Credit Activated Term ID Excluded Transaction ID International Fee indicator Application ID Application ID Suffix Minimum due Snapshot Account Dipute_Out_Number Ptntl_frd_Transaction Flag Statement Beginning Current Date and Time Statement Date Account Number Account Number Original Force Post Flag Multiple Payment Reversal Indicator Non-Sufficient Funds Cross-Cycle Indicator Outstanding type Post Date Post Time potnl_frd_move flag Reference number Reverse Indicator Transaction Authorisation Transaction Display Flag Transaction Fraud Flag Transaction memo Flag Transaction Account Function Transaction Source Terminal Entry 1.48793E+11 298455992 5748168 1.48793E+11 532.1998989 Activate 20-06-2023 20-06-2023 800.9873725 980.6900951 20-06-2023 20-06-2023 831.9393703 1.257929668 1.243545411 Fail Mobile B Yes Yes 4 Low Online Purchase B 1.9483E+11 1.358310142 1.33402116 3.161405319 Type2 72 ['75340', '65583', '82194', '72557'] 20-06-2023 2.191223936 Riggs Group South Michael WI Argentina Merchant14182 Yes B L2 Yes Auth19740 Cap1 ID2 Attr2 Acc1 Char2 PS2 Class2 Debit Terminal1 Q2 Ref68772 INR Resp48363 Matched CreditTerm72479 N CreditTerm95669 ExclTxn87978 Yes AppID99973 PInh6UC8Eq 77.17963198 Dispute0 Yes 06-07-2023 20:50 20-06-2023 Acc71996 AccOrig20548 Yes No Yes Type2 20-06-2023 20-06-2023 No Ref30819 No Auth38619 Yes No No Function1 Source1 Entry3 4.74925E+11 222238145 7520312 4.74925E+11 124.297479 Expired 05-07-2023 05-07-2023 445.6898336 701.8382662 05-07-2023 05-07-2023 470.9749958 1.901066897 1.28784316 Fail Mobile A No No 9 Low Mobile Payment B 2.70642E+11 1.596193632 1.970957542 3.899791365 Type3 78 ['63244', '60026', '15835', '39788'] 05-07-2023 9.454337896 Smith-Bradley Port Angela NV Sao Tome and Principe Merchant66199 Yes C L3 No Auth12644 Cap3 ID2 Attr1 Acc1 Char2 PS3 Class2 Debit Terminal3 Q3 Ref81045 INR Resp59634 Matched CreditTerm17380 Y CreditTerm88691 ExclTxn86178 Yes AppID39191 MPTQjNIJGJ 66.49280204 Dispute1 No 06-07-2023 20:50 05-07-2023 Acc19326 AccOrig89356 No Yes Yes Type1 05-07-2023 05-07-2023 No Ref27568 Yes Auth48926 No No Yes Function1 Source3 Entry1 1.26968E+11 115566789 3273159 1.26968E+11 434.1310879 Activate 04-07-2023 04-07-2023 284.2505582 582.1825448 04-07-2023 04-07-2023 411.5087524 1.164641221 1.186334999 Fail Web B Yes No 7 Medium Retail Store Purchase B 6.27495E+11 0.169976948 1.212949429 6.536199857 Type2 94 ['65254', '75552', '10673', '14536'] 04-07-2023 1.724718089 Sullivan and Sons Emmaton PA Sierra Leone Merchant24016 Yes C L3 No Auth41287 Cap3 ID3 Attr1 Acc2 Char2 PS1 Class3 Debit Terminal2 Q2 Ref48994 RUB Resp91856 Not Matched CreditTerm33867 Y CreditTerm51754 ExclTxn32505 No AppID41386 TOrjAqS9HW 67.20968037 Dispute2 No 06-07-2023 20:50 04-07-2023

In [ ]:
from pyspark.sql.functions import col
duplicates_df = df.groupBy("id").count().where(col("count") > 1)
display(duplicates_df)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-1339745766189296>:2
      1 from pyspark.sql.functions import col
----> 2 duplicates_df = df.groupBy("id").count().where(col("count") > 1)
      3 display(duplicates_df)

NameError: name 'df' is not defined

In [ ]:
from pyspark.sql.functions import col, date_format
from pyspark.sql.types import DateType, StringType

# This code is used to convert date columns in the DataFrame to a specific date format, displaying the modified DataFrame, while handling any exceptions and capturing execution result information for notebook termination.

def convert_columns_to_date_format(df):
    schema = df.schema
    date_format_expr="yyyy-MM-dd"

    # Iterate through each column in the DataFrame
    for column_name in df.columns:
        # Get the data type of the current column
        column_data_type = schema[column_name].dataType
        # Check if the column is of DateType
        if isinstance(column_data_type, DateType):
            # Convert the column to the specified date format and cast it to StringType
            df = df.withColumn(column_name, date_format(col(column_name), date_format_expr).cast(StringType()))

    return df
try:
    df = convert_columns_to_date_format(df)
    display(df)
except Exception as exp:
    exp=str(exp)
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
    # Terminate the notebook execution and provide the JSON object as the exit value
    dbutils.notebook.exit(my_json)

id Member ID Snapshot Date Social Security Access Number Primary Owner Access Number Partition Key Birth Date Last Contact Date Last Activity Date Original MBRP Date Credit Date Last Update Date DBR Run ID Full Name First Name Middle Name Last Name Prefix Name Suffix Name Eighteen Plus Indicator Party Status Code Party type Membership Type Code Business Membership Flag Membership Flag Create Date Member init open date Member last activity Date Gender Code Primary language type code Employment Status Code Designation Salary Military Brach Code/Military service code Military Rank Code Origin Code/Membership Origin Type code test New_Column 556366084287 867065563 10/23/2022 246-44-6608 8269324287 1681754655 1 4/21/1980 10/20/2022 07-02-2023 12/27/2022 04-06-2023 6/18/2023 9828 Stephanie Hinton Paul Randy Lewis Mr. MD FALSE A Organization Silver FALSE TRUE 9/27/2022 07-04-2023 07-10-2022 F Spanish Unemployed Barrister 292151 Navy Corporal In-person null New_Value 843876207923 104418438 12/27/2022 576-33-7620 569277923 1853291463 3 7/18/1991 09-12-2022 5/19/2023 10-09-2022 1/20/2023 8/30/2022 70303 Thomas Thomas April Angela Gutierrez Mr. MD FALSE C Organization Bronze FALSE TRUE 4/19/2023 08-12-2022 09-11-2022 F English Employed Psychologist, educational 55994 Air Force Sergeant Online null New_Value 596969735817 145705969 5/22/2023 502-37-6973 12345 67890 1 09-01-1988 5/21/2023 4/29/2023 7/18/2022 2/25/2023 3/30/2023 56088 Amber Berry Abhishek Singh Dustin Ballard Mrs. Jr. TRUE B Organization Gold TRUE FALSE 9/20/2022 8/31/2022 7/20/2022 M French Employed Youth worker 528805 Navy Private In-person null New_Value 049912530939 263120499 10/26/2022 609-82-1253 1433770939 8505549789 2 09-03-1985 3/24/2023 2/27/2023 11-02-2022 06-06-2023 8/31/2022 21518 Diana Estrada Nicole Julie Harris Ms. Jr. FALSE C Individual Bronze TRUE TRUE 8/25/2022 3/29/2023 11/26/2022 F English Unemployed Private music teacher 699328 Army Sergeant Referral null New_Value 082297466091 839690822 9/15/2022 500-34-9746 9155766091 8755337242 2 04-05-1945 10/15/2022 3/31/2023 1/18/2023 12/26/2022 02-03-2023 84847 Jordan Hart Linda Kevin Harrison Mrs. MD FALSE B Organization Gold FALSE FALSE 7/21/2022 10-05-2022 11/22/2022 M Spanish Employed Medical secretary 717998 Navy Sergeant In-person null New_Value 321559118540 247573215 01-10-2023 794-56-5911 57868540 1081231221 2 2/24/1935 5/20/2023 02-12-2023 6/22/2023 01-10-2023 12-05-2022 21328 Danielle Ballard Sara Douglas Holloway Mr. DVM TRUE C Individual Bronze FALSE FALSE 12/13/2022 5/26/2023 10/16/2022 F English Unemployed Merchandiser, retail 547882 Navy Sergeant Referral null New_Value 282752022028 190552827 07-04-2023 290-37-5202 1744372028 5013190999 1 10/26/1940 9/30/2022 01-10-2023 3/22/2023 03-06-2023 06-11-2023 1037 Sylvia Mccann Amber Dylan Watkins Mrs. DDS TRUE B Individual Bronze TRUE TRUE 10/15/2022 10-10-2022 12-06-2022 F English Unemployed Research officer, political party 668563 Navy Private Online null New_Value 796935226698 209917969 04-02-2023 615-52-3522 5500636698 2543371385 3 07-09-1962 03-09-2023 8/27/2022 11-10-2022 5/23/2023 6/28/2023 59083 Natalie Hamilton Adam Maureen Harrison Mr. DDS FALSE C Organization Gold TRUE TRUE 7/14/2022 10-08-2022 05-01-2023 M English Unemployed Equities trader 458175 Air Force Corporal Online null New_Value 082872324773 291000828 02-02-2023 354-11-7232 3792814773 6509973689 1 08-08-1950 10-01-2022 12/31/2022 1/26/2023 7/27/2022 9/28/2022 55371 Angela Garcia Sarah Madison Washington Mrs. DDS FALSE B Organization Silver TRUE FALSE 6/16/2023 2/18/2023 02-01-2023 F English Unemployed Risk manager 448264 Air Force Sergeant Referral null New_Value 481041379649 972974810 02-05-2023 886-71-4137 5188759649 2108205472 3 10/24/1997 03-08-2023 4/23/2023 2/25/2023 3/16/2023 03-02-2023 82905 Kelli Ramirez Teresa Mark Miles Mr. MD FALSE A Organization Bronze FALSE FALSE 4/28/2023 07-08-2022 5/30/2023 M Spanish Unemployed Senior tax professional/tax inspector 610693 Navy Corpora

In [ ]:
from pyspark.sql.functions import col

# This code is used to convert a 'id' column in the DataFrame to string type, displaying the modified DataFrame and its count, while handling any exceptions and capturing execution result information for notebook termination.

def convert_column_to_string(df, column_name):
    # Convert a specific column in the DataFrame to string type
    df = df.withColumn(column_name, col(column_name).cast('string'))
    return df
try:
    # Call the convert_column_to_string function to convert the 'id' column to string type
    df = convert_column_to_string(df, 'id')
    display(df)
    display(df.count())
except Exception as exp:
    exp=str(exp)
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
    # Terminate the notebook execution and provide the JSON object as the exit value
    dbutils.notebook.exit(my_json)

In [ ]:
# This code is used to define the configuration settings for connecting to Azure Cosmos DB and prints the master key, container name, and database name for verification purposes.

cfg = {
    # Configuration settings for connecting to Azure Cosmos DB
    "spark.cosmos.accountEndpoint" : f"https://{cosmosDBaccount}.documents.azure.com:443/",
    "spark.cosmos.accountKey" : cosmosMasterKey,
    "spark.cosmos.database" : cosmosDatabaseName,
    "spark.cosmos.container" : cosmosContainerName,
    # "Upsert": "true"
}
# Print the Azure Cosmos DB master key, container name, and database name
print(cosmosMasterKey)
print(cosmosContainerName)
print(cosmosDatabaseName)

manqeohdZHGr3uZjuV9cJvajsSp6hFppGyib64ZeE7AdpBEDZcBdJ3ipS6hX9V4OpiwxAXOrhQN5ACDb0w4kug==
account_details
BankingDataset


In [ ]:
from pyspark.sql import DataFrameWriter
from pyspark.sql.functions import col, to_date, date_format

# This code is used to handle writing a DataFrame to Azure Cosmos DB, capturing any errors, and providing execution result information for notebook termination.

def write_to_cosmos(df, cfg):
    try:
        writer = DataFrameWriter(df)
        # Write the DataFrame to Azure Cosmos DB using the specified target type and configuration
        writer.format(target_Type).mode("append").options(**cfg).save()
        print("Data written to Cosmos DB successfully!")
        return df
    except Exception as e:
        print("An error occurred while writing to Cosmos DB:", e)
        raise Exception(f"An error occurred while writing to Cosmos DB: {e}")
        
try:
    # Call the write_to_cosmos function to write the DataFrame to Azure Cosmos DB
    df = write_to_cosmos(df, cfg)
    if df is not None:
        record_inserted = df.count()
    else:
        record_inserted = 0
except Exception as exp:
    exp=str(exp)
    print(exp)
    exp=exp.partition(":")[0]
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":exp,"system_id":system_id}
    # Terminate the notebook execution and provide the JSON object as the exit value
    dbutils.notebook.exit(my_json)


Data written to Cosmos DB successfully!


In [ ]:
try:
# This code is used to read data from Azure Cosmos DB into a DataFrame, displaying the count and contents of the DataFrame, while handling and capturing any exceptions that occur.

    df = spark.read.format(target_Type).options(**cfg) \
        .option("spark.cosmos.read.inferSchema.enabled", "true") \
        .load()
    print(df.count())
    display(df)
except Exception as exp:
    my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":str(exp),"system_id":system_id}
    dbutils.notebook.exit(my_json)

41


test Prefix Name Suffix Name Party Status Code Member init open date Last Activity Date First Name Last Name Access Number Last Contact Date Origin Code/Membership Origin Type code Primary Owner Access Number Original MBRP Date Social Security Business Membership Flag Member ID Membership Flag Party type Create Date Last Update Date id Gender Code Full Name Birth Date Military Brach Code/Military service code Middle Name Employment Status Code Snapshot Date Eighteen Plus Indicator Salary Membership Type Code DBR Run ID Partition Key Primary language type code Designation Member last activity Date Credit Date Military Rank Code null Mr. MD B 10/19/2022 3/13/2023 Edward Petersen 3543121744 04-07-2023 Online 2465122235 01-07-2023 330-20-7654 FALSE 122759787 FALSE Organization 4/22/2023 11/30/2022 978776541744 M Nancy Coleman 7/27/1997 Air Force John Employed 8/29/2022 FALSE 686948 Silver 77831 8 English Buyer, retail 11/13/2022 11-02-2022 Sergeant null Mx. MD A 1/26/2023 8/25/2022 Kenneth Newman 156092609 12/30/2022 In-person 9618730481 1/19/2023 625-04-1412 FALSE 236030917 TRUE Individual 02-11-2023 7/16/2022 091714122609 F Troy Sims 10/31/2000 Navy Angela Unemployed 5/31/2023 FALSE 560692 Gold 94742 1 French Television camera operator 6/22/2023 08-02-2022 Corporal null Dr. DDS A 11/15/2022 08-04-2022 Reginald Berg 4051667438 8/28/2022 Referral 7546523439 12/13/2022 410-27-2300 TRUE 449478040 FALSE Organization 03-04-2023 9/17/2022 804023007438 M Kurt Ellis 12/15/1964 Navy Kristina Employed 5/30/2023 FALSE 956513 Bronze 33189 10 French Regulatory affairs officer 07-06-2022 08-02-2022 Corporal null Mr. DVM A 12/31/2022 9/14/2022 Adrian Coleman 9815623839 10-12-2022 Referral 870320939 06-07-2023 269-19-5906 FALSE 303073902 FALSE Organization 7/24/2022 7/25/2022 390259063839 M Roy Pace 1/29/1997 Navy Joanna Employed 10/25/2022 FALSE 152528 Gold 18726 10 English Communications engineer 03-06-2023 1/27/2023 Sergeant null Ms. Jr. C 3/29/2023 2/27/2023 Nicole Harris 1433770939 3/24/2023 Referral 8505549789 11-02-2022 609-82-1253 TRUE 263120499 TRUE Individual 8/25/2022 8/31/2022 049912530939 F Diana Estrada 09-03-1985 Army Julie Unemployed 10/26/2022 FALSE 699328 Bronze 21518 2 English Private music teacher 11/26/2022 06-06-2023 Sergeant null Mrs. DDS A 05-08-2023 11-03-2022 Cynthia Jones 5359681843 04-01-2023 Referral 884046611 2/19/2023 220-90-2219 FALSE 191839115 FALSE Organization 12/20/2022 12-09-2022 911522191843 F Michael Serrano 4/16/1962 Air Force John Unemployed 10/18/2022 TRUE 490145 Gold 63979 4 English Agricultural engineer 07-05-2023 10/14/2022 Sergeant null Ind. DDS A 03-08-2023 8/20/2022 Whitney Bush 3487297649 12-02-2022 Online 4930864538 9/30/2022 579-47-8337 TRUE 748615849 FALSE Organization 04-03-2023 1/28/2023 584983377649 F Justin Salinas 11/18/1954 Army John Unemployed 07-11-2022 FALSE 267225 Silver 74087 3 Spanish Clinical scientist, histocompatibility and immunogenetics 8/31/2022 12/30/2022 Sergeant 4 MD FALSE Organization 7/16/2022 09-05-2022 Lisa Dr. 1262423335 9/26/2022 Referral 1610079207 03-10-2023 574-70-3998 TRUE 252315455 8/27/2022 white 6/16/2023 59534 545539983335 French Ronald 08-08-2022 Sergeant Edwards Electronics engineer 09-04-2022 B engg FALSE John Gomez 3/17/1950 Employed 886538 F 03-08-2023 In-person 5 MD FALSE Organization 02-06-2023 10/24/2022 Robert Mr. 4349179974 08-11-2022 In-person 7804433175 1/25/2023 793-29-8821 TRUE 326004437 1/28/2023 Gold 8/31/2022 53832 443788219974 Spanish Charles 1/21/2023 Corporal Guzman Nutritional therapist 9/13/2022 A Army TRUE Jacqueline Fry 03-08-1974 Employed 690413 F 3/30/2023 In-person 10 DDS FALSE Organization 09-10-2022 8/22/2022 Lydia Mr. 3392198246 11-07-2022 Online 6596677929 04-11-2023 837-97-0993 FALSE 853480075 6/30/2023 Bronze 1/24/2023 28290 007509938246 English Theresa 10/29/2022 Private Dalton Horticultural consultant 12/27/2022 C Air Force FALSE Lisa Johnson 04-04-1982 Unemployed 249179 F 5/20/2023 Online null Ind. Jr. C 3/19/2023 11/29/2022

In [ ]:
# This code is used to capture and provide information for notebook execution results.

my_json={"records_read":records_read,"record_inserted":record_inserted,"trigged_by":trigged_by,"exception":'',"system_id":system_id}
dbutils.notebook.exit(my_json)